## Finalizing the coadd sample
### This sample will potentially be used in a short ApJ Letter as well as follow up with MANGA

10-8-16 Claudia and I looked at all the coadd images (in /documents/) and picked out those which were the best examples of clumpy galaxies for additional follow-up/study. 

What needs to be done:
    1. Isolate these galaxies from the FITS file containing all clumpy gals -- send coordinates to Chris?
    2. Download all available SDSS spectra for each galaxy
    3. Get all single-epoch imaging 
    4. Look at overall subject distributions

In [1]:
from astropy.table import Table, join
from astropy.coordinates import SkyCoord
from astropy import units as u
import numpy as np
import matplotlib.pyplot as plt
import matplotlib
%matplotlib inline

/home/oxymoronic/.local/lib/python2.7/site-packages/IPython/kernel/__init__.py:13: ShimWarning: The `IPython.kernel` package has been deprecated. You should import from ipykernel or jupyter_client instead.
  "You should import from ipykernel or jupyter_client instead.", ShimWarning)


In [2]:
# Import FITS file containing ALL clumpy gals (coadd, single) with associated SDSS metadata
data = Table.read('../data/gzh_sdss_strictclumpy_trueclumpy_sdssdata.fits')

In [3]:
coadd_mask = data['Table'] != 'sdss_single  '
coadd = data[coadd_mask]
print len(coadd)

105


In [4]:
# Remove duplicates! (only)

c1 = SkyCoord(coadd['RA']*u.degree, coadd['DEC']*u.degree)
c2 = SkyCoord(coadd['RA']*u.degree, coadd['DEC']*u.degree)
idxc1, idxc2, d2d, d3d = c1.search_around_sky(c2, 25*u.arcsec)

print "These are the duplicate images in the coadd sample:"
print np.where(np.bincount(idxc1)>1)

coadd_dupes = np.array([6,14,15,32,40,47,61,71,76,101,103,104])

dupe_mask = np.ones(len(coadd), dtype='bool')
dupe_mask[coadd_dupes] = False

cc = coadd['RA','DEC'][dupe_mask]
# This csv file for finding associated spectra in CasJobs (ALL COADD CLUMPY)
cc.write('../data/gzh_nodupes_coadd_coordlist.csv',format='ascii.csv')

These are the duplicate images in the coadd sample:
(array([  5,   6,  13,  14,  15,  31,  32,  39,  40,  46,  47,  60,  61,
        70,  71,  75,  76, 100, 101, 102, 104]),)


In [5]:
# Claudia and I went through and will exclude some objects which aren't very good clumpy examples
#  (exclude crappy clumps AND duplicates which aren't good coords for that obj)
exclude_idx = np.array([1,6,15,16,22,26,30,33,34,37,41,48,57,61,64,72,73,77,78,80,84,90,94,102,104,105])

exclude_mask = np.ones(len(coadd), dtype='bool')
exclude_mask[exclude_idx-1] = False

final_cc = coadd[exclude_mask]
# csv file for finding associated spectra in CasJobs  (FINAL SAMPLE COADD CLUMPY)
coords = final_cc['OBJID','RA','DEC']
coords.write('../data/gzh_nodupes_coadd_coordlist_finalsample.csv',format='ascii.csv')
final_cc.write('../data/gzh_nodupes_coadd_finalsample.fits',overwrite=True)

In [6]:
old_rcparams = dict(matplotlib.rcParams)  # this makes a *copy*

In [7]:
matplotlib.rcParams.update({'font.size': 18, 'font.family': 'STIXGeneral', 'mathtext.fontset': 'stix'})

with_z = np.where(~np.isnan(final_cc['REDSHIFT']))
#print final_cc['RA','DEC'][np.where(np.isnan(final_cc['REDSHIFT']))]

# Sample distributions
fig = plt.figure(figsize=(10,10))

ax = fig.add_subplot(221)
ax.hist(final_cc['REDSHIFT'][with_z], histtype='stepfilled', color='purple', alpha=.75)
ax.set_xlabel('redshift')
ax.set_xticks([0., 0.04, 0.08, 0.12, 0.16])
ax.set_xticklabels(['0.0', '0.04', '0.08', '0.12', '0.16'])
ax.text(0.06, 10, '{0} out of {1} gals \n     with z'.format(len(with_z[0]), len(final_cc)))

ax = fig.add_subplot(222)
ax.hist(final_cc['PETROR90_R'], normed=True, histtype='step', color='k', lw=2, label='All')
ax.hist(final_cc['PETROR90_R'][with_z], normed=True, histtype='stepfilled', color='purple', 
        alpha=0.75, label='With z')
ax.set_xlabel('PetroR90_r (arcsec)')
ax.legend(loc='best',frameon=False)

ax = fig.add_subplot(223)
ax.hist(final_cc['PETROMAG_G'], normed=True, histtype='step', color='k', lw=2, label='All')
ax.hist(final_cc['PETROMAG_G'][with_z], normed=True, histtype='stepfilled', color='purple', 
        alpha=0.75, label='With z')
ax.set_xlabel('Petromag_G')

In [8]:
# Grab the list of spectra associated with the final_cc galaxies -- see /data/readme.md for details
spectra = Table.read('../data/gzh_nodupes_coadd_finalsample_spectralist.csv')


name = []
ra, dec = [], []
num_spectra, avg_z = [], []

gals = spectra.group_by('Name')
for grp in gals.groups:
    name.append(grp['Name'][0])
    ra.append(grp['RA'][0])
    dec.append(grp['Dec'][0])
    num_spectra.append(len(grp))
    avg_z.append(np.mean(grp['Redshift']))
                 
    print grp['Name'][0], grp['RA'][0], grp['Dec'][0], len(grp), np.mean(grp['Redshift'])

spectra_overview = Table(data=(name, ra,dec,num_spectra,avg_z,), 
                         names=('OBJID', 'ra', 'dec', 'NUM_SPEC', 'AVG_Z'))
spectra_overview['options'] = ['S' for g in ra]

8647474690314995238 315.5565 -1.19793 1 0.0997
8647474690329084045 347.67491 -1.16347 1 0.0123
8647474690334458050 0.01343 -1.11304 2 0.0218
8647474690339438847 11.39126 -1.10173 3 0.0137333333333
8647474690343043368 19.51206 -1.16639 1 0.0399
8647474690344747089 23.42261 -1.15827 2 0.01645
8647474690858942711 331.69223 -0.68814 2 0.02915
8647474690860843214 336.01355 -0.7244 1 0.1183
8647474690867986516 352.3223 -0.6734 2 0.11955
8647474690881749069 23.7141 -0.65855 3 0.0397666666667
8647474690883846156 28.50213 -0.75274 4 0.01595
8647474690885157080 31.61629 -0.65106 1 0.0641
8647474690887909597 37.86103 -0.79292 2 0.04055
8647474690887909626 37.8843 -0.72761 2 0.0089
8647474690889483420 41.48939 -0.75341 2 0.05395
8647474690891186220 45.2636 -0.74329 6 0.0379333333333
8647474691387491512 312.71863 -0.3255 2 0.03065
8647474691388014990 313.83986 -0.4136 1 0.0539
8647474691389784776 317.92962 -0.24889 1 0.061
8647474691400204480 341.69743 -0.26382 1 0.0268
8647474691404202093 350.8243

In [9]:
from SDSSutils.jpegs import jpegCreator as JC

In [10]:
# I have a list for all the galaxies with spectra -- let's make urls for them!
# To do this (best), I need the size of the galaxy. So read in another file... 

dr12_ancillary = Table.read('../data/clumpy_coadd_imaging_highzgal_0.csv')

missing_spectra = [objid for objid in dr12_ancillary['OBJID'] if objid not in spectra_overview['OBJID']]
missing_idx = []
for missing in missing_spectra:
    missing_idx.append(np.where(dr12_ancillary['OBJID']==missing)[0][0])

mask = np.ones(len(dr12_ancillary), dtype='bool')
mask[missing_idx] = False

size = np.array([0.2*rad for rad in dr12_ancillary['petrorad_r'][mask]])

urls = []
for r, d,s in zip(ra,dec,size):
    jpg = JC.jpegURL(ra=r, dec=d, width=s/2., height=s/2, options='S')
    urls.append(jpg.url)

spectra_overview['location'] = urls

In [11]:
from display_jpegs import *

In [12]:
spec_join = join(spectra_overview, dr12_ancillary[mask], keys='OBJID')
print spec_join.colnames

['OBJID', 'ra_1', 'dec_1', 'NUM_SPEC', 'AVG_Z', 'options', 'location', 'objID1', 'ra_2', 'dec_2', 'run', 'rerun', 'camcol', 'field', 'type', 'petroMag_u', 'petroMag_g', 'petroMag_r', 'petroMag_i', 'petroMag_z', 'petrorad_u', 'petrorad_g', 'petrorad_r', 'petrorad_i', 'petrorad_z', 'extinction_u', 'extinction_g', 'extinction_r', 'extinction_i', 'extinction_z']


In [13]:
show_jpegs(spec_join)